In [2]:
import matplotlib.pyplot as plt
%matplotlib inline
import pandas as pd
import numpy as np
import pickle
from ckiptagger import data_utils, construct_dictionary, WS, POS, NER
import re
#import jieba
from ckip_transformers.nlp import CkipWordSegmenter
import csv

2022-12-26 22:51:10.729861: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-12-26 22:51:11.266876: I tensorflow/core/util/util.cc:169] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2022-12-26 22:51:11.462586: E tensorflow/stream_executor/cuda/cuda_blas.cc:2981] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2022-12-26 22:51:13.122915: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: li

In [3]:
course_df_original = pd.read_csv('../data/courses.csv').fillna('')
course_df = course_df_original.drop(['course_id', 'teacher_id', 'course_published_at_local', 'course_published_at_local', 'course_price'], axis=1)
course_df['description'] = course_df['description'].replace('([\<]).*?([\>])','',regex=True)
course_df = course_df.replace('\n', '',regex=True)
course_df = course_df.replace('[\d_]', '',regex=True).astype(str)
course_df.insert(0, 'course_id', course_df_original['course_id'])
course_df[:2]

course_id           course_name  \
0  61888e868f154b000781b45a  少女人妻華麗變身：七大妝容七彩的夢幻樂園   
1  54d5a117065a7e0e00725ac0         幾何圖形分割 X 色塊組合   

                                       teacher_intro groups      sub_groups  \
0  在美妝 KOL 圈裡屬個人風格強烈的 Alice，在清新與叛逆風格間遊刃有餘，其幽默的美妝影...   生活品味  更多生活品味,護膚保養與化妝   
1  從學生時代開始摸索photoshop等軟體，自以為有些天賦但後來發現其實沒有。出社會後從事美...  藝術,設計      平面設計,繪畫與插畫   

         groups+subgroups               topics  \
0  生活品味更多生活品味,生活品味護膚保養與化妝       更多生活品味,護膚保養與化妝   
1          設計平面設計,藝術繪畫與插畫  Illustrator/以拉,配色技巧   

                                         description  \
0  少女人妻第一堂線上課程，跟著我一起華麗變身！在社群上許多人經常問我：「為什麼人妻畫的妝那麼好...   
1  這是一個有趣的小技巧，主要利用illustrator裡面的&quot;分割“這個功能，我已經...   

                              will_learn                 required_tools  \
0            不再害怕各種顏色的彩妝，可以更隨心搭配各種繽紛的顏色。            所需工具為：視課程實際會用到的彩妝用品   
1  可以將任何區塊分割成自己想要的幾何圖形、快速的上色，並且能夠應用在許多地方  Adobe Illustrator（必備）, camera   

                              recommended_background           target_group  
0  只要你有一顆愛化妝、想變漂亮的心皆可以參加。⚠️ 雖然課程當中會帶到相關彩妝技巧，不過內容偏...                 熱愛彩妝的人  
1                            知道如何使用Illustrator的基本工具列  每一位興趣的人都能學得來，非常容易的小技巧

In [4]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
import datetime
from scipy.sparse import csr_matrix

In [5]:
info = []
for i in range(course_df.shape[0]):
    t = course_df.loc[i, :].values.flatten().tolist()
    info.append([t[0], ' '.join(t)])
info = pd.DataFrame(info, columns = ['course_id', 'text'])
info[:5]

course_id                                               text
0  61888e868f154b000781b45a  61888e868f154b000781b45a 少女人妻華麗變身：七大妝容七彩的夢幻樂園 ...
1  54d5a117065a7e0e00725ac0  54d5a117065a7e0e00725ac0 幾何圖形分割 X 色塊組合 從學生時代開始...
2  54d5d9952246e60a009ec571  54d5d9952246e60a009ec571 數位拼貼的手感 自由工作者，致力於品牌視覺...
3  54d7148a2246e60a009ec588  54d7148a2246e60a009ec588 Line 的貼圖自己動手做！ 我是Dann...
4  5513e92b38239d10005778e1  5513e92b38239d10005778e1 為申請學校或工作寫好英文自傳 在北美長大，...

In [6]:
info

course_id  \
0    61888e868f154b000781b45a   
1    54d5a117065a7e0e00725ac0   
2    54d5d9952246e60a009ec571   
3    54d7148a2246e60a009ec588   
4    5513e92b38239d10005778e1   
..                        ...   
723  6191c002a20c140006edcfcd   
724  60ee8d419b2ee60007c940cf   
725  61b941f2e8990300069e4e9e   
726  6164fd2cc74856000619aa16   
727  607ceae6fa76bb60e8a556c8   

                                                  text  
0    61888e868f154b000781b45a 少女人妻華麗變身：七大妝容七彩的夢幻樂園 ...  
1    54d5a117065a7e0e00725ac0 幾何圖形分割 X 色塊組合 從學生時代開始...  
2    54d5d9952246e60a009ec571 數位拼貼的手感 自由工作者，致力於品牌視覺...  
3    54d7148a2246e60a009ec588 Line 的貼圖自己動手做！ 我是Dann...  
4    5513e92b38239d10005778e1 為申請學校或工作寫好英文自傳 在北美長大，...  
..                                                 ...  
723  6191c002a20c140006edcfcd Home appétit！在地食材打造道地...  
724  60ee8d419b2ee60007c940cf 偵探攻略：推理詭計X故事創作 寫作課 本來...  
725  61b941f2e8990300069e4e9e 在家輕鬆做  款健康無負擔高含水歐式麵包 ...  
726  6164fd2cc74856000619aa16 Zunni 美甲全科班：從質感設計開始創業...  
727  607ceae6fa76bb60e8a556c8 MultiCharts：期貨新手懶人投資術...  

[728 rows x 2 columns]

In [5]:
ws_driver = CkipWordSegmenter(model="bert-base", device=0)
ws = ws_driver(info)


Inference: 100%|██████████| 1/1 [00:00<00:00,  1.45it/s]


In [8]:
cat = []
for section in ws:
    cat.extend(section)

In [9]:
print(cat)

['course_id', 'text']


In [7]:
ws = WS('./ckip/data')

/home/ian/miniconda3/envs/adlhw3/lib/python3.8/site-packages/ckiptagger/model_ws.py:106: UserWarning: `tf.nn.rnn_cell.LSTMCell` is deprecated and will be removed in a future version. This class is equivalent as `tf.keras.layers.LSTMCell`, and will be replaced by that in Tensorflow 2.0.
  cell = tf.compat.v1.nn.rnn_cell.LSTMCell(hidden_d, name=name)
2022-12-26 22:51:20.733998: E tensorflow/stream_executor/cuda/cuda_driver.cc:265] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected
2022-12-26 22:51:20.734068: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (TaiwanFarmer): /proc/driver/nvidia/version does not exist
2022-12-26 22:51:22.562341: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX_VNNI FMA
To enable them in other o

In [8]:
tfidf_ml = TfidfVectorizer(stop_words='english')
tfidf_ml.fit(info.text)

# TF-IDF Dicitonary
dictionary = dict(zip(tfidf_ml.get_feature_names_out(), list(tfidf_ml.idf_)))

# feature name
tfidf_feature = tfidf_ml.get_feature_names()

/home/ian/miniconda3/envs/adlhw3/lib/python3.8/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


In [9]:
len(dictionary.keys())

174145

In [10]:
for keys,values in dictionary.items():
    print(keys)
    print(values)

54d5a117065a7e0e00725ac0
6.898526551448713
54d5d9952246e60a009ec571
6.898526551448713
54d7148a2246e60a009ec588
6.898526551448713
54f1268f4ec3c809002e4a29
6.898526551448713
551171a938239d1000577864
6.898526551448713
551198a738239d1000577870
6.898526551448713
5513e92b38239d10005778e1
6.898526551448713
551a6be023774e0a001eb20c
6.898526551448713
55307d94d530a90a00a3a896
6.898526551448713
55599687dfe21b0a00e776d9
6.898526551448713
556ad58777a8710900bedffe
6.898526551448713
557ad62bd736230f00adb2ab
6.898526551448713
5591501e6dec460f00111314
6.898526551448713
5593f992cfe8320b00ccd4c4
6.898526551448713
559a217dcfe8320b00ccd75b
6.898526551448713
559e49185850311000fca504
6.898526551448713
55a4d6397b4d99100011957d
6.898526551448713
55ae208a7b4d9910001198f2
6.898526551448713
55ae34247b4d99100011990d
6.898526551448713
55ae36c87b4d99100011990f
6.898526551448713
55ae66017b4d991000119959
6.898526551448713
55b0ba667b4d991000119a92
6.898526551448713
55c636d27b4d99100011a4aa
6.898526551448713
55e3dccbfa2

In [11]:
tfidf_feature[:10]

['54d5a117065a7e0e00725ac0',
 '54d5d9952246e60a009ec571',
 '54d7148a2246e60a009ec588',
 '54f1268f4ec3c809002e4a29',
 '551171a938239d1000577864',
 '551198a738239d1000577870',
 '5513e92b38239d10005778e1',
 '551a6be023774e0a001eb20c',
 '55307d94d530a90a00a3a896',
 '55599687dfe21b0a00e776d9']

In [267]:
# #Construct the required TF-IDF matrix by fitting and transforming the data
# vectorizer = TfidfVectorizer(stop_words= 'english')
# tfidf_matrix = vectorizer.fit_transform(info)

# #print(tfidf.vocabulary_)
# tfidf_matrix_nd = tfidf_matrix.T.toarray()
# #np.save('tfidf_embedding/item_embeddings_english.npy', tfidf_matrix_nd)
# df = pd.DataFrame(tfidf_matrix_nd, index=vectorizer.get_feature_names_out ())

In [12]:
from gensim.models.word2vec import Word2Vec

w2v_model = Word2Vec(info.text.apply(lambda text: text.split()))
w2v_vocab = list(w2v_model.wv.index_to_key)
print(w2v_model)

Word2Vec<vocab=1314, vector_size=100, alpha=0.025>


In [13]:
starttime = datetime.datetime.now()

# TF-IDF weighted Word2Vec
tfidf_text_vect = [] # tfidf-w2v is stored in this list
row = 0

for text in info.text.apply(lambda text: text.split()):
    text_vect = np.zeros(100)
    weight_sum = 0
    for word in text:
        if word in w2v_vocab and word in tfidf_feature:
            vec = w2v_model.wv[word]
            tf_idf = dictionary[word]*(text.count(word)/len(text))
            text_vect += (vec * tf_idf)
            weight_sum += tf_idf
    if weight_sum != 0:
        text_vect /= weight_sum
    tfidf_text_vect.append(text_vect)
    row += 1

# calculate running time
endtime = datetime.datetime.now()
print("建立模型時間: ",endtime - starttime)



建立模型時間:  0:02:58.322284


In [14]:
def Preprocess(text):
    rule = re.compile(r'[^a-zA-Z0-9\u4e00-\u9fa5]')
    text = rule.sub(' ',str(text))
    text = re.sub(' +', '',text)
    text = re.sub(' ', '',text)
    text = ws([text], sentence_segmentation=True)
    text = [x for l in text for x in l]
    return text

In [15]:
def recommend_law(text, tfidf_text_vect = tfidf_text_vect, top_k = 50):
    text = Preprocess(text)
    text_vect = np.zeros(100) # w2v size
    weight_sum = 0
    for word in text:
        if word in w2v_vocab and word in tfidf_feature:
            vec = w2v_model.wv[word]
            tf_idf = dictionary[word]*(text.count(word)/len(text))
            text_vect += (vec * tf_idf)
            weight_sum += tf_idf
    if weight_sum != 0:
        text_vect /= weight_sum
    tmp_vect = [*tfidf_text_vect,text_vect]
    new_cos_sim = cosine_similarity(tmp_vect, tmp_vect)
    sim_score = np.sort(new_cos_sim[new_cos_sim.shape[0]-1])[::-1][1:top_k+1]
    tmp_top_k = info[['text']].iloc[np.argsort(new_cos_sim[new_cos_sim.shape[0]-1])[::-1][1:top_k+1]]
    tmp_top_k['similarity_score'] = [round(score*100,1) for score in sim_score]
    
    return tmp_top_k



In [26]:
starttime = datetime.datetime.now()

newtext = '職場技能_更多職場技能'
result = recommend_law(newtext)

# calculate running time
endtime = datetime.datetime.now()
print("搜尋推薦時間: ",endtime - starttime)
result

搜尋推薦時間:  0:00:00.265228


text  similarity_score
61   56c1e3b3e91d590900234105 創業必備：前端網頁設計入門 Jeremy ...             100.0
240  5af1c528b44939001e4637b6 玩轉 Unity! 零基礎打造自己的 D ...             100.0
595  5fd24f017687e53b086c7fe7 SQL的五十道練習：初學者友善的資料庫入門...             100.0
79   56a3ace74ec4c609007d3065 Processing - 讓程式碼說設計語...             100.0
511  5f506991b1b6d678526889e1 數位轉型敲門磚，產業必學 AI 思維通識課...             100.0
149  593a0a69d0472a0700f24243 解碼程式思維－物件導向的靈魂 Gavin，...             100.0
151  598b01e6891876070047423a MATLAB 音訊處理入門 - 專屬語音助...             100.0
350  5c82809d9d98460020c3078d 開啟你的 AI 技能 —— 無痛入門 NL...             100.0
113  58677d39f108e00800c25f36 C 語言入門特訓 行動創客學院 執行長長庚...             100.0
719  610814069871100007ab7b4f Python 的 + 練習：資料科學學習手...             100.0
218  5aca2dc9d21aee001e55b296 經典駭客攻擊教程：給每個人的網站安全入門 ...             100.0
403  5de8fec16117240026540b9c Github 免費架站術！輕鬆打造個人品牌...             100.0
615  5ef484ec96fb8b534ac9018b 入門數據分析，掌握 Hive SQL 取數...             100.0
127  591c480a00f58c0700788178 漫遊程海 | Python 入門到製作遊戲...             100.0
120  58cb3438da45810700e53507 開啟資料科學的學習大門 - R入門教學 W...             100.0
157  59ae5da5cd5792070055b973 資料庫設計 - 有效的使用系統資料 華碩高...              99.9
316  5ce792eaea2d0500209a9389 一支燈學打光，家裡就是攝影棚 大家好，我是...              99.9
659  60aeac37bca91777bf5bb114 Node.js、MongoDB 網站後端工...              99.9
701  5e68a440e612310028027e40 遊戲譯者必備：掌握日文遊戲翻譯要領 米耶翻...              99.9
257  5b31bbf82c4c440043919aae 用手機捕捉瞬息美好-IPPA 冠軍的攝影心...              99.9
623  60a784719591b7394cb554e4 搞懂主管小劇場，向上管理職場攻心計 新激梗...              99.9
67   572be49fd60bb3090091d208 讓圖不只是好看的－資訊設計思考力！ 由專業...              99.9
239  5b3b080baa5ff8001e22316e Evernote，你的無壓工作術 你的數位...              99.9
690  60e7f0598036260006b71683 主理人思維：服飾品牌創業入門課 【準心設計...              99.9
225  5acb00ded21aee001e55b670 簡報方舟：高效簡報的系統化做法 你好，我們...              99.9
678  6039f9ad1f5b5b279b5183d5 業務力必備 - 高效達標的精準銷售術！ 新...              99.9
233  5baf7243c3964c001eebcd8d 大學生必修的  堂簡報課 「大學生必修的堂...              99.9
228  5afe4dad7d3f43001e61b8a2 啾啾鞋的資料彙整術 - 別淹沒在資訊海！ ...              99.9
394  5dd935075e4baa002072a10a 一次搞懂專案管理 - 從入門到業界實務 原...              99.9
175  59d61b0d1f6685001ee6a2bb Unity 遊戲開發- [進階篇] 打造堆...              99.9
493  5e689828e612310028027876 產品數據分析 - 打造網路產品的決策引擎 ...              99.9
629  6057068f2023d5f5a2e306bb 吃早餐學食物攝影：一週晨間美感養成 Oni...              99.9
210  5a2a6b3fa6501f001e2e9e86 全方位學 WordPress - 從架站到...              99.9
374  5db7c35221050f00219bc498 Katie 凱蒂流動瑜珈：啟動熱能，身心修...              99.9
220  5a6f15aee77921001e624ee9 TOEIC — 全方位攻略  新制多益！ ...              99.9
199  5a7baad0b6ba47006f5660f0 英語教父教你輕鬆戰勝新多益聽力 美明尼蘇達...              99.9
101  5864e19cf108e00800c24f7a 吉他從零開始-Fingerstyle（進階...              99.9
500  5f7c209762ad22756c7a1c74 Today at Apple:和攝影師 A...              99.9
378  5d7cf0a645639e00212cc8af 英文寫作經典指南：個流暢俐落的必備法則 專...              99.9
642  608004cb2ff403488b9f5eb9 用簡報操縱會議結論的《五階段提案誘導術》 ...              99.9
648  60792df91c463c4c395baa11 輕鬆發聲！質感說話！ 堂課讓您說話不疲勞 ...              99.9
469  5ed1d148598c2ae575bec29f 職場溝通管理學：打造團隊好關係與高績效 H...              99.9
276  5bf381c53b78f00020b44fdc 好想法好好說 - 潘月琪的堂質感說話課 橫...              99.9
298  551198a738239d1000577870 超人氣吸睛表達力－職場必學表達課！ 教學超...              99.9
502  5f7c212262ad2203e77a1cc9 Today at Apple:和攝影師 P...              99.9
575  5fe22e7fe810e10fc483dd78 Java 工程師必備！Spring Boo...              99.9
78   57728810c2917a110075fb68 克服阻礙，快速說出流暢英文 多益暨英文口說...              99.9
608  6040818e043b47f89a5c8f41 職場英文大補帖｜銀行行員必備的英文口說 C...              99.9
273  5bf3e5562dcfe6002005618b 訪談溝通術：交流、說服與談判的必勝訣竅 你...              99.9
145  598053e0acc137070007186a 在台灣也能學一口漂亮英文！Phonics ...              99.9

In [56]:
test_unseen = pd.read_csv('../data/test_unseen.csv')
test_unseen

user_id                 course_id
0      5f1dc5a3afdc0537b5de8979  6156a77fdf426a0007cc5fe1
1      5f432175a32a53813a24e1a5  6156a77fdf426a0007cc5fe1
2      5a93a2b844a1e4001eee7a26  6156a77fdf426a0007cc5fe1
3      617ec17d1a87ca000710ce8f  6156a77fdf426a0007cc5fe1
4      614c3233e64756000603277d  6156a77fdf426a0007cc5fe1
...                         ...                       ...
11092  61cf079c1647a30006557fc0  6156a77fdf426a0007cc5fe1
11093  5f54a406f24eac7d75f12cfa  6156a77fdf426a0007cc5fe1
11094  61cf1fec2a965800074634b6  6156a77fdf426a0007cc5fe1
11095  5e8f93b33856b2f1f465aeca  6156a77fdf426a0007cc5fe1
11096  61a7271d617d83000629acc7  6156a77fdf426a0007cc5fe1

[11097 rows x 2 columns]

In [28]:
seen_predict_df = pd.read_csv('../data/test_unseen.csv')

In [30]:
userlist = pd.read_csv('../data/users.csv')

In [31]:
userlist

user_id  gender      occupation_titles  \
0       54ccaa73a784960a00948687  female                    NaN   
1       54dca4456d7d350900e86bae    male                    NaN   
2       54e421bac5c9c00900cd8d47  female                    NaN   
3       54e961d4c5c9c00900cd8d84   other                    金融業   
4       54e9b744c5c9c00900cd8d8a   other  資訊科技,法律、社會及文化專業,非營利組織   
...                          ...     ...                    ...   
130561  62e09de8fc3d3500060d4211  female                    NaN   
130562  62f0823a8c4414000667c592     NaN                    NaN   
130563  631b86242145060007efc7dd     NaN                    NaN   
130564  6331648104ed0f000610dfd2    male                   公務人員   
130565  6358a7599c01ba344812d24d    male                 服務業,其他   

                                                interests   recreation_names  
0       職場技能_創業,藝術_電腦繪圖,設計_介面設計,設計_動態設計,設計_平面設計,投資理財_投...                NaN  
1       設計_動態設計,設計_平面設計,設計_應用設計,程式_程式入門,程式_程式語言,藝術_角色設...                NaN  
2       設計_平面設計,職場技能_資料彙整,藝術_繪畫與插畫,行銷_數位行銷,職場技能_文書處理,職...                NaN  
3       投資理財_理財,攝影_影像創作,投資理財_投資觀念,藝術_更多藝術,音樂_樂器,投資理財_金...                NaN  
4       程式_網頁前端,投資理財_理財,投資理財_投資觀念,程式_程式語言,設計_設計理論,投資理財...   政治經濟,社會服務,舞台劇,電影  
...                                                   ...                ...  
130561  語言_英文,設計_介面設計,設計_網頁設計,設計_設計理論,程式_軟體程式開發與維護,行銷_...                NaN  
130562                                                NaN                NaN  
130563                                                NaN                NaN  
130564          投資理財_理財,攝影_影像創作,攝影_後製剪輯,攝影_商業攝影,投資理財_投資觀念  旅行旅遊,運動健身,金融理財,電影  
130565  音樂_人聲,藝術_手寫字,藝術_色彩學,藝術_電腦繪圖,生活品味_靈性發展,藝術_素描,生活...           瑜珈,舞蹈,貓派  

[130566 rows x 5 columns]

In [37]:
def create_combination(x):

    gender = x['gender']
    occupation_titles = x['occupation_titles']
    interests = x['interests']
    recreation_names = x['recreation_names']
    text = str(gender) + str(occupation_titles) + str(interests) + str(recreation_names)
    return text
userlist['combination'] = userlist.apply(create_combination, axis=1)
userlist['combination'].head(2)

0    femalenan職場技能_創業,藝術_電腦繪圖,設計_介面設計,設計_動態設計,設計_平面...
1    malenan設計_動態設計,設計_平面設計,設計_應用設計,程式_程式入門,程式_程式語言...
Name: combination, dtype: object

In [38]:
userlist

user_id  gender      occupation_titles  \
0       54ccaa73a784960a00948687  female                    NaN   
1       54dca4456d7d350900e86bae    male                    NaN   
2       54e421bac5c9c00900cd8d47  female                    NaN   
3       54e961d4c5c9c00900cd8d84   other                    金融業   
4       54e9b744c5c9c00900cd8d8a   other  資訊科技,法律、社會及文化專業,非營利組織   
...                          ...     ...                    ...   
130561  62e09de8fc3d3500060d4211  female                    NaN   
130562  62f0823a8c4414000667c592     NaN                    NaN   
130563  631b86242145060007efc7dd     NaN                    NaN   
130564  6331648104ed0f000610dfd2    male                   公務人員   
130565  6358a7599c01ba344812d24d    male                 服務業,其他   

                                                interests   recreation_names  \
0       職場技能_創業,藝術_電腦繪圖,設計_介面設計,設計_動態設計,設計_平面設計,投資理財_投...                NaN   
1       設計_動態設計,設計_平面設計,設計_應用設計,程式_程式入門,程式_程式語言,藝術_角色設...                NaN   
2       設計_平面設計,職場技能_資料彙整,藝術_繪畫與插畫,行銷_數位行銷,職場技能_文書處理,職...                NaN   
3       投資理財_理財,攝影_影像創作,投資理財_投資觀念,藝術_更多藝術,音樂_樂器,投資理財_金...                NaN   
4       程式_網頁前端,投資理財_理財,投資理財_投資觀念,程式_程式語言,設計_設計理論,投資理財...   政治經濟,社會服務,舞台劇,電影   
...                                                   ...                ...   
130561  語言_英文,設計_介面設計,設計_網頁設計,設計_設計理論,程式_軟體程式開發與維護,行銷_...                NaN   
130562                                                NaN                NaN   
130563                                                NaN                NaN   
130564          投資理財_理財,攝影_影像創作,攝影_後製剪輯,攝影_商業攝影,投資理財_投資觀念  旅行旅遊,運動健身,金融理財,電影   
130565  音樂_人聲,藝術_手寫字,藝術_色彩學,藝術_電腦繪圖,生活品味_靈性發展,藝術_素描,生活...           瑜珈,舞蹈,貓派   

                                              combination  
0       femalenan職場技能_創業,藝術_電腦繪圖,設計_介面設計,設計_動態設計,設計_平面...  
1       malenan設計_動態設計,設計_平面設計,設計_應用設計,程式_程式入門,程式_程式語言...  
2       femalenan設計_平面設計,職場技能_資料彙整,藝術_繪畫與插畫,行銷_數位行銷,職場...  
3       other金融業投資理財_理財,攝影_影像創作,投資理財_投資觀念,藝術_更多藝術,音樂_樂...  
4       other資訊科技,法律、社會及文化專業,非營利組織程式_網頁前端,投資理財_理財,投資理財...  
...                                                   ...  
130561  femalenan語言_英文,設計_介面設計,設計_網頁設計,設計_設計理論,程式_軟體程式...  
130562                                       nannannannan  
130563                                       nannannannan  
130564  male公務人員投資理財_理財,攝影_影像創作,攝影_後製剪輯,攝影_商業攝影,投資理財_投...  
130565  male服務業,其他音樂_人聲,藝術_手寫字,藝術_色彩學,藝術_電腦繪圖,生活品味_靈性發...  

[130566 rows x 6 columns]

In [ ]:
import csv

predict_users = seen_predict_df["user_id"].to_list()
with open("predict.csv", "w") as f:
    writer = csv.writer(f)
    writer.writerow(["user_id", "course_id"])
    for user_id in predict_users:
        for user_id in userid:
            
        recommend = " ".join(recommend_law())
        writer.writerow([user_id, recommend])

In [ ]:
#想法 尚未實作:找userid in userlist對應combination 放進recommen_law()